In [3]:
from openai import OpenAI
client = OpenAI()

completion = client.chat.completions.create(
  model="gpt-4o-mini-2024-07-18",
  messages=[
    {"role": "system", "content": "You are a poetic assistant, skilled in explaining complex programming concepts with creative flair."},
    {"role": "user", "content": "Compose a poem that explains the concept of recursion in programming."}
  ]
)

print(completion.choices[0].message)

ChatCompletionMessage(content="In the heart of code where patterns dance,  \nLies a concept, simple, yet full of chance.  \nRecursion is the name, a loop of its own,  \nA function that calls, yet is never alone.  \n\nPicture the trees, with branches that reach,  \nEach leaf a reflection, a lesson to teach.  \nA function you call, and it calls back again,  \nUnfolding the layers like petals of rain.  \n\nFirst take a step back, define your base case,  \nFor without this anchor, it races with haste.  \nLike a lighthouse in fog, it guides through the storm,  \nStopping the cycle, where chaos could swarm.  \n\nThen boldly you venture, the call to repeat,  \nWith a problem reduced, oh, how bittersweet!  \nEach time it resolves, the picture grows clear,  \nLike echoing whispers that progress near.  \n\nFibonacci numbers, the factorial's might,  \nEach step builds upon, in recursive delight.  \nLike Russian dolls nested, compact and profound,  \nIn each function’s folds, solutions are found. 

In [4]:
def describe_theorem(theorem_code):
    prompt = f"Please explain this lean 4 theorem in 3 sections: Description, Break-down, Applications: {theorem_code}"
    completion = client.chat.completions.create(
      model="gpt-4o-mini-2024-07-18",
      messages=[
        {"role": "system", "content": "You are a mathematician who can understand lean 4 theorems."},
        {"role": "user", "content": prompt}
      ]
    )
    response = completion.choices[0].message
    return response.content

response = describe_theorem("theorem Asymptotics.IsBigOWith.of_bound{α : Type u_1} {E : Type u_3} {F : Type u_4} [Norm E] [Norm F] {c : ℝ} {f : α → E} {g : α → F} {l : Filter α} :(∀ᶠ (x : α) in l, ‖f x‖ ≤ c * ‖g x‖) → Asymptotics.IsBigOWith c l f g")
print(response)

Here's a breakdown of the Lean 4 theorem `Asymptotics.IsBigOWith.of_bound`.

### Description
This theorem states that if a function `f` is bounded by a constant multiple of another function `g` for a large enough set of inputs (as described by a filter `l`), then `f` is asymptotically big O of `g` with respect to the same filter `l`. In formal terms, it expresses that if, for a sufficiently large set of inputs (as captured by the filter), the norm of `f x` is less than or equal to a constant `c` multiplied by the norm of `g x`, then we can conclude that `f` is big O of `g` with respect to the filter.

### Break-down
1. **Types and Structures**: The theorem is set in a context where:
   - `α` is an arbitrary type (typically representing some input domain).
   - `E` and `F` are types representing output spaces, which have norms (`Norm E` and `Norm F`).
   - `c` is a real number, which acts as the bounding constant.
   - `f` and `g` are functions from `α` to `E` and `F`, respectively.
   

In [5]:
import os
#print(os.getenv("GITHUB_ACCESS_TOKEN", None))

from lean_dojo import *

repo = LeanGitRepo(
    #"https://github.com/leanprover-community/mathlib4",
    #"27c6744e1c0e25d676be5eb252cd4b6d30c6acc7",
    "https://github.com/leanprover-community/mathematics_in_lean",
    "210802794074c003ddf237ee56a0bf1fb5a9fe10"
)

repo

LeanGitRepo(url='https://github.com/leanprover-community/mathematics_in_lean', commit='210802794074c003ddf237ee56a0bf1fb5a9fe10')

In [6]:
import pickle

fin = open('/home/mcwave/code/axiomatization/datasets/traced_repo_mathinlean_20240702.pkl', 'rb')
traced_repo = pickle.load(fin)
fin.close()

In [ ]:
import json

print(len(traced_repo.traced_files), "files in total")

input_path = '/home/mcwave/code/axiomatization/datasets/traced_repo_mathinlean_20240702_gpt-Copy1.json'
existing_theorems = set()
fin = open(input_path, 'r')
existing_results = json.load(fin)
fin.close()
for full_path, full_name, code, response in existing_results:
    existing_theorems.add(full_path + full_name)

print(len(existing_theorems), "existing theorems")
    
results = []

output_path = '/home/mcwave/code/axiomatization/datasets/traced_repo_mathinlean_20240702_gpt_part_2.json'

for traced_file in traced_repo.traced_files:
    full_path = str(traced_file.lean_file.path)
    print("PATH:", full_path)
    if 'Mathlib' not in full_path:
        continue
    for premise in traced_file.get_premise_definitions():
        code = premise['code']
        full_name = premise['full_name']
        if full_path + full_name in existing_theorems:
            continue
        if 'theorem' not in code:
            continue
        print("FULL_NAME:", full_name)
        try:
            response = describe_theorem(code)
            results.append((full_path, full_name, code, response))
        except Exception as e:
            print(e)
            continue
        if len(results) % 10 == 0:
            print(len(results), "processed")
            fout = open(output_path, 'w')
            fout.write(json.dumps(results))
            fout.close()

3143 files in total
14841 existing theorems
PATH: MIL/C04_Sets_and_Functions/S03_The_Schroeder_Bernstein_Theorem.lean
PATH: MIL/C02_Basics/S04_More_on_Order_and_Divisibility.lean
PATH: MIL/C02_Basics/S03_Using_Theorems_and_Lemmas.lean
PATH: MIL/C04_Sets_and_Functions/S01_Sets.lean
PATH: MIL/C05_Elementary_Number_Theory/S03_Infinitely_Many_Primes.lean
PATH: MIL/C05_Elementary_Number_Theory/S02_Induction_and_Recursion.lean
PATH: MIL/C07_Hierarchies/S03_Subobjects.lean
PATH: MIL/C07_Hierarchies/S02_Morphisms.lean
PATH: MIL/C07_Hierarchies/S01_Basics.lean
PATH: MIL/C09_Topology/S01_Filters.lean
PATH: MIL/C10_Differential_Calculus/S01_Elementary_Differential_Calculus.lean
PATH: MIL/C02_Basics/S05_Proving_Facts_about_Algebraic_Structures.lean
PATH: MIL/C04_Sets_and_Functions/S02_Functions.lean
PATH: MIL/C11_Integration_and_Measure_Theory/S02_Measure_Theory.lean
PATH: MIL/C09_Topology/S03_Topological_Spaces.lean
PATH: MIL/C10_Differential_Calculus/S02_Differential_Calculus_in_Normed_Spaces.le

PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Function/AEEqOfIntegral.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Function/Jacobian.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Integral/IntegrableOn.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Function/StronglyMeasurable/Basic.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Function/LpSeminorm/Basic.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Integral/Marginal.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Function/L1Space.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Integral/DivergenceTheorem.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Integral/Average.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Function/SimpleFuncDenseLp.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Constructions/Polish.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureTheory/Constructions/BorelSpace/Metric.lean
PATH: .lake/packages/mathlib/Mathlib/MeasureT

PATH: .lake/packages/mathlib/Mathlib/Tactic/Explode/Pretty.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Positivity/Basic.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Linter/Lint.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/FunProp/Types.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Explode/Datatypes.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Widget/Conv.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Widget/Congrm.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Ring/PNat.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Ring/RingNF.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Attr/Register.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/FunProp/Core.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Linter/HashCommandLinter.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Widget/SelectPanelUtils.lean
PATH: .lake/packages/mathlib/Mathlib/GroupTheory/PresentedGroup.lean
PATH: .lake/packages/mathlib/Mathlib/Tactic/Attr/Core.lean
PATH: .lake/packages/mathlib/Mathli

PATH: .lake/packages/mathlib/Mathlib/Data/Nat/GCD/BigOperators.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Finsupp/Encodable.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Nat/Cast/Order.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Countable/Defs.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Nat/Choose/Sum.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Nat/Choose/Basic.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Finsupp/Antidiagonal.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Nat/Cast/Prod.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Finsupp/Fin.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Countable/Basic.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Nat/Factorization/PrimePow.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Finite/Set.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Finsupp/ToDFinsupp.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Nat/Factorization/Basic.lean
PATH: .lake/packages/mathlib/Mathlib/Data/Finite/Card.lean
PATH: .lake/packages/mathlib/Mathlib/D

FULL_NAME: Real.sqrt_eq_zero'
FULL_NAME: Real.sqrt_ne_zero
FULL_NAME: Real.sqrt_ne_zero'
FULL_NAME: Real.sqrt_pos
FULL_NAME: Real.sqrt_mul
FULL_NAME: Real.sqrt_mul'
FULL_NAME: Real.sqrt_inv
FULL_NAME: Real.sqrt_div
FULL_NAME: Real.sqrt_div'
10 processed
FULL_NAME: Real.div_sqrt
FULL_NAME: Real.sqrt_div_self'
FULL_NAME: Real.sqrt_div_self
FULL_NAME: Real.lt_sqrt
FULL_NAME: Real.sq_lt
FULL_NAME: Real.neg_sqrt_lt_of_sq_lt
FULL_NAME: Real.lt_sqrt_of_sq_lt
FULL_NAME: Real.lt_sq_of_sqrt_lt
FULL_NAME: Real.nat_sqrt_le_real_sqrt
FULL_NAME: Real.real_sqrt_lt_nat_sqrt_succ
20 processed
FULL_NAME: Real.real_sqrt_le_nat_sqrt_succ
FULL_NAME: Real.floor_real_sqrt_eq_nat_sqrt
FULL_NAME: Real.nat_floor_real_sqrt_eq_nat_sqrt
FULL_NAME: Real.sqrt_one_add_le
FULL_NAME: Filter.Tendsto.sqrt
FULL_NAME: ContinuousWithinAt.sqrt
FULL_NAME: ContinuousAt.sqrt
FULL_NAME: ContinuousOn.sqrt
FULL_NAME: Continuous.sqrt
PATH: .lake/packages/mathlib/Mathlib/Data/List/Pairwise.lean
FULL_NAME: List.Pairwise.forall_of_for

...

Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: min_mul_distrib
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: min_mul_distrib'
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: o

Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: Units.zero_lt
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: mul_lt_mul_of_lt_of_le₀
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NA

Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: act_rel_of_rel_of_act_rel
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: rel_act_of_rel_of_rel_act
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_qu

Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: abs_dvd_self
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: dvd_abs
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: self_dvd_abs


Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: Int.abs_lt_one_iff
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NAME: Int.abs_le_one_iff
Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}
FULL_NA

In [8]:
len(existing_theorems)

570

In [18]:
traced_repo.traced_files[150].get_premise_definitions()[10]['code']

'@[simp]\ntheorem integrableOn_empty : IntegrableOn f ∅ μ'